# Interactive visualisation tutorial

In the [introductory_tutorial](introductory_tutorial.ipynb) we ran through building structural covariance network analyses using `scona`🍪, in the [global_network_viz_tutorial](global_network_viz_tutorial.ipynb) we looked at how to report measures relating to the whole network, and in the [anatomical_viz_tutorial](anatomical_viz_tutorial.ipynb) we made some static visualisions that you could use to report your findings in a published paper.

In this tutorial we'll cover some interactive and 3D connectome visualisation commands.

You'll be able to share these with your final publication for your readers to explore.

Click on any of the links below to jump to that section
* [Get set up](#Get-set-up) (make sure to run this section before jumping into any of the others!)
* [Visualise nodes in 3D: `view_nodes_3d`](#Visualise-nodes-in-3D%3A-%3Ccode%3Eview_nodes_3d%3C%2Fcode%3E)
* [Visualise Connectome in 3D: `view_connectome_3d`](#Visualise-Connectome-in-3D%3A%3Ccode%3Eview_connectome_3d%3C%2Fcode%3E)
* [Plot Connectome: `plot_connectome`](#Plot-Connectome%3A-%3Ccode%3Eplot_connectome%3C%2Fcode%3E)

## Get set up

### Import the modules you need

In [ ]:
import scona as scn
import scona.datasets as datasets
import numpy as np
import networkx as nx
import pandas as pd
from IPython.display import display

import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

%load_ext autoreload
%autoreload 2

### Read in the data, build a network and calculate the network metrics

If you're not sure about this step, please check out the [introductory_tutorial](introductory_tutorial.ipynb) notebook for more explanation.

In [ ]:
# Read in sample data from the NSPN WhitakerVertes PNAS 2016 paper.
df, names, covars, centroids = datasets.NSPN_WhitakerVertes_PNAS2016.import_data()

# calculate residuals of the matrix df for the columns of names
df_res = scn.create_residuals_df(df, names, covars)

# create a correlation matrix over the columns of df_res
M = scn.create_corrmat(df_res, method='pearson')

# Initialise a weighted graph G from the correlation matrix M
G = scn.BrainNetwork(network=M, parcellation=names, centroids=centroids)

# Threshold G at cost 10 to create a binary graph with 10% as many edges as the complete graph G.
G10 = G.threshold(10)

# Calculate global and nodal measures for graph G10
G10.calculate_global_measures()
G10.calculate_nodal_measures()

## Visualise nodes in 3D: `view_nodes_3d`

One of the first things you'll want to do is view the nodes of your network on the brain.

The commands here are lightly wrapping around the excellent [nilearn.plotting.view_markers](http://nilearn.github.io/modules/generated/nilearn.plotting.view_markers.html#nilearn.plotting.view_markers) tool.

### Look at the data

We'll use the thresholded graph `G10` because it has some of the properties we'd like to visualise.

The nodes have specific attributes, or you can see all of the information saved for each node using the `report_nodal_measures` command.

In [ ]:
# Look at one specific node's attributes
G.nodes[12]

In [ ]:
# show the nodal attributes of first 5 brain regions
G10.report_nodal_measures().loc[:5]

One of the most important columns is the `centroids` column which has the x, y and z coordinates of the nodal location in MNI space.
We'll use those values to put the nodes in the right place on the brain.

### Import the code you need: `view_nodes_3d`

In [ ]:
# import the function to plot network measures
from scona.visualisations import view_nodes_3d

### Plot nodes

As it says in the name: lets view the nodes on a 3d plot.

All you need is a graph (we're using `G10` in this case) which has the `centroids` attribute.

#### Default settings

By default, all nodes will be displayed in **black** color with the same size value: **5.0**.

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10)
# Show the view interactively
ConnectomeView

#### Spin the brain around

Have a play around!

You should be able to view the brain from different angles by moving the mouse to rotate the brain.
Alternatively you can select one of six prescribed orientations by using the drop down lis in the bottom left corner

#### Zoom in and out

You can zoom in on the brain either by selecting the 🔍 icon, or using two fingers on the trackpad, and then dragging the mouse.

#### Move the brain from left to right

You can pan the image from side to side by clicking on the 4 direction arrow icon and then moving the mouse.

#### Reset the view

Sometimes you can make the brain look particularly odd (very small, very large, or upside down, for example!)
The home button (🏠) will rest the view to the default settings, which is a nice way to get back on track.

#### Adjust the transparency of the brain

You can make the brain on which the nodes are plotted more or less transparent by moving the slider along the horizonal bar in the bottom left corner.

Note that this will not change the colour of the nodes, just the brain in the background.

#### Save a picture

You can save the brain (in the orientation you've selected) as a `png` file by clicking the camera icon (📷) in the top right corner.
(That menu might not always be visible.
It should appear when you hover your mouse in that corner though!)

The image will be saved wherever your browser saves images by default, so if in doubt check your `Downloads` folder.

#### Edit the image with plotly

It's a little confusing that the save icon (💾) doesn't save an image (that's the 📷 icon as described above) but rather opens the plot in [Plotly:Chart Studio](https://plot.ly/create/).

Plotly is a little hard to get started with, but once you're up and running it can give you online control over setting up the image.

You can modify and manually plot the nodes location and colors using the data in the top right of the page.
And you can pan and set different rotations when you're visualising the brain.

***Explore and find what you need!*** Have fun 😺

### Plot nodes with different sizes and change the default color

You might want to adjust the size of the nodes according to their **degree**: making the most strongly connected nodes larger than those with fewer connections.

The degree is saved in the nodal measures pandas data frame and we can pass that column directly to the `view_nodes_3d` function under the `node_size` keyword arguement.

Note that we've changed the `node_color` to "coral" because black dots are very boring 😉

In [ ]:
# Get the nodal measures as a pandas dataframe
nodal_df = G10.report_nodal_measures()

# Create a view
ConnectomeView = view_nodes_3d(G10, node_color="coral", node_size=nodal_df['degree'])

# Show the view interactively
ConnectomeView

WOAH! That's not what we were expecting!

The circles that mark the nodes are all overlapping.
This is _not_ a particularly useful figure.

The reason is that the range of degree values is too large.
The smallest dots look great, but the largest dots are taking up too much space.

You can play around with different scalings by dividing the values by a constant and/or adding a constant.
You may remember this activity from high school mathematics.
If you don't, here's a [lovely refresher video](https://www.khanacademy.org/math/ap-statistics/random-variables-ap/transforming-random-variables/v/impact-of-scaling-and-shifting-random-variables) from Khan Academy 📐👩‍🔬

For example, for this example dataset, adding **30.0** to every degree value and dividing by **7.0** looks pretty good.

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, node_color="coral", node_size=(nodal_df['degree']+30)/7.0)
# Show the view interactively
ConnectomeView

If you want to show a different measure, **participation coefficient** for example, you'll need to customise the values again.

Play around with the two different options in the cell below by uncommenting one of the lines with information for `node_size` to contrast the different sizes and their effect on the brain image.

1. No adjustment (nodes will look very small)
2. Add a constant (10, nodes will all look very similar in size)
3. Multiple the values by a constant (20, the nodes in frontal cortex with low participation coefficient look much smaller than those with higher participation coefficient)

None of the node size options are _wrong_ but they do tell quite different stories!
Remember to be responsible in the choices you make when you communicate your findings.
With great power ... 💪

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10,
                               node_color="cornflowerblue",
                               #node_size=(nodal_df['participation_coefficient'])
                               #node_size=(nodal_df['participation_coefficient']+10.0)
                               node_size=(nodal_df['participation_coefficient']*20.0)
                              )
# Show the view interactively
ConnectomeView

### Show a subset of the nodes

If you set the node size to **0** then it will not be shown on the brain.

A good use case for this is if you want to show the location of just one specific node.
Let's say: `lh_rostralmiddlefrontal_part1`.

In [ ]:
# Create a list that has 0s everwhere except for that one node
sizes = [ 15 
          if node_name == 'lh_rostralmiddlefrontal_part1' 
          else 0 
          for node_name in nodal_df['name'].values ]

print (sizes)

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, node_color="Red", node_size=sizes)

# Show the view interactively
ConnectomeView

#### Plot the rich club only

Another use case is to plot just the rich club nodes.

To do this you need to define a cut off point from the rich club curve (described in more detail in the [global_network_viz](global_network_viz.ipynb) tutorial).
In the published paper that this example data is from we designated the most connected 15% of nodes to be in the rich club.


In [ ]:
# Define the degree threshold that separates the rich club from
# the other nodes
rich_thresh = np.percentile(nodal_df['degree'], 85)
print ('Rich club threshold: {}'.format(rich_thresh))

# Create a list that replaces the degree value with 0 for nodes that are
# not in the rich club
sizes = [ degree 
          if degree > rich_thresh 
          else 0 
          for degree in nodal_df['degree'].values ]

# Print the sizes to show the 0s and values
print (sizes)

# Adjust these values as above (otherwise you'll get some great big circles again!)
sizes = [ (size + 30.0)/7.0 
          if size > 1.0
          else 0
          for size in sizes ]

# Print just the first few entries
print (sizes[:5])

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, node_color="teal", node_size=sizes)

# Show the view interactively
ConnectomeView

### Plot nodes in different colors

You might not want all your nodes in the same colour.

For example you might want to put each hemisphere in a different colour.

MNI coordinates are set up so that the `x` coordinate of a node determines whether a node belongs to the left or right hemisphere.

Negative values of `x` mean that node is in left hemisphere, and positive values are all located in the right hemisphere.

In [ ]:
# Set 2 colors for nodes in the left and right hemispheres
color_dict = {'left' : "#FFD700",
              'right' : "#4169E1"}

# Create a list of colors for each node
node_colors = [ color_dict['left'] if x < 0 else color_dict['right'] for x in nodal_df['x'] ]

# Print every 10th node (to save us from a huge print out!)
print (node_colors[::10])

Do you see that in our case the nodes are ordered so that all the ones in the left hemisphere come first and then those in the right hemisphere?

That's a coincidence of the way this data was stored.
It doesn't have to be that way at all.
The important information is the `x` coordinate in the nodal values data frame (`nodal_df`).

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, node_color=node_colors)

# Show the view interactively
ConnectomeView

Fun right? [Go Bears!](https://150.berkeley.edu/story/cals-blue-gold-and-bear) 🐻

### Plot nodal measures in different colours using a colourmap

We can grab the nodal values from the `nodal_df` dataframe, and use a colourmap instead of specifying individual colours for each value.

This example uses a keyword argument we haven't seen yet: **measure**.
Measure looks for columns in the nodal values data frame and uses the information it finds in there to set the **colour**.

Note that you can't use this syntax (yet?) to change the node size because it is very difficult to automatically set the correct scaling factors (as you saw above!)

#### Show modules in different colours using a qualitative colourmap

We want the modules to be as different from each other as possible, so in the example below we've chosen the `tab10` colourmap from this [awesome list of options](https://matplotlib.org/examples/color/colormaps_reference.html)!

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, measure='module', cmap_name='tab10')

# Show the view interactively
ConnectomeView

#### Visualise continuous data with a range of colours

Set the **continuous** parameter to `True` in order to plot nodes according to the continuous data of nodal measures (like "closeness", "betweenness" etc).

In the example below we've shown how `closeness` varies across the brain.

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, 
                               measure="closeness", 
                               cmap_name="autumn",
                               continuous=True)

# Show the view interactively
ConnectomeView

These values all look kinda super similar, and it's probably driven by some nodal values that are particularly high or particularly low.

If you want to adjust the min and max values of the colorbar you can do that with the `vmin` and `vmax` parameters.

This usually lets you see a little more variation in the remaining 80% of the data, but be careful that you don't lie about the data as you adjust these values!

In [ ]:
# Set vmin and vmax to be the 10th and 90th percentiles of the data range
vmin = np.percentile(nodal_df['closeness'], 10)
vmax = np.percentile(nodal_df['closeness'], 90)

In [ ]:
# Create a view
ConnectomeView = view_nodes_3d(G10, 
                               measure="closeness", 
                               cmap_name="autumn",
                               continuous=True, 
                               vmin=vmin,
                               vmax=vmax)

# Show the view interactively
ConnectomeView

## Visualise Connectome in 3D: `view_connectome_3d`

Wow, we've done loads of visualisations with the nodes, but what about the **edges** of the graph!?

With the `scona.view_nodes_3d()` tool we were mainly focused to show only nodes and especially node visualisation according to their nodal measures.
Whereas `view_connectome_3d` tool is essentially used to show the connections between nodes.

This function builds off the lovely [nilearn.plotting.view_connectome](http://nilearn.github.io/modules/generated/nilearn.plotting.view_connectome.html#nilearn.plotting.view_connectome) tool.


### Look at the data

In [ ]:
# Print the number of edges
print ('Number of edges in original graph: {}'.format(G.number_of_edges()))
print ('Number of edges in thresholded (10%) graph: {}'.format(G10.number_of_edges()))

In [ ]:
# Print the weight of a couple of example edges
print ('Edge between {} and {}'.format(G.node[144]['name'],G.node[300]['name']))
print ('  Weight in original graph: {:2.3f}'.format(G.edges[(144, 300)]['weight']))
print ('  Weight in thresholded (10%) graph: {:2.3f}'.format(G10.edges[(144, 300)]['weight']))

print ('Edge between {} and {}'.format(G.node[256]['name'],G.node[260]['name']))
print ('  Weight in original graph: {:2.3f}'.format(G.edges[(256, 260)]['weight']))
print ('  Weight in thresholded (10%) graph: {:2.3f}'.format(G10.edges[(256, 260)]['weight']))

### Use original graph rather than the thresholded graph

As you can see from looking at the data, all the edges in thresholded network are exactly 1.0.

We create a thresholded network and then binarize it (setting weights to 1 or 0) so that we can calculate the global and nodal measures for the graph.

However, if we plotted **all** those connections (even "only" the 10% we kept for `G10`) the network would look like a messy spagetti plot!
And as the weights are all exactly the same we have no way to select, for example, the top 2% of edges (which generally makes a good looking network).

Therefore, for the `view_connectome_3d` function its important to pass the **original Graph** (`G`) rather than the thresholded graph (`G10`).

There is a useful inbuilt argument `edge_threshold` that makes it easier to adjust which edges to show.

### Import the code you need: `view_connectome_3d`

In [ ]:
from scona.visualisations import view_connectome_3d

### View Connectome

The view connectome function lets you view the edges - the connections - of the network.

You need an unthresholded graph (we're using `G`) which has the `centroids` attribute.

#### Default settings

By default, all nodes have **3.0** size and the top 2% of edges are displayed.

The color of each edge is chosen based on the `weight` value of an edge, which corresponds to the strangth of the correlation between the two regions across your cohort.

The default colormap for visualising edges is `Spectral_r`.

In [34]:
# plot all edges in G
view_connectome_3d(G)

C:\ProgramData\Anaconda3\envs\kwpython3\lib\site-packages\nilearn\plotting\js_plotting_utils.py:103: UserWarning: It seems you have created more than 10 nilearn views. As each view uses dozens of megabytes of RAM, you might want to delete some of them.
  warnings.warn('It seems you have created more than 10 '


In [ ]:
from nilearn import plotting
from scona.visualisations_helpers import graph_to_nilearn_array

In [ ]:
adj_matrix, node_coords = graph_to_nilearn_array(G)

edge_threshold="98%"

plotting.view_connectome(adjacency_matrix=adj_matrix,
                         node_coords=node_coords,
                         edge_threshold=edge_threshold)

Displaying 47278 edges does not convey any useful information and does not illustrate any findings from brain analysis. Therefore let's set the edge threshold.

**edge_threshold** : str, number or None, optional (default=None)  
If None, no thresholding. If it is a number only connections of amplitude greater than threshold will be shown. If it is a string it must finish with a percent sign, e.g. “25.3%”, and only connections of amplitude above the given percentile will be shown.

### View connectome with edge thresholding

To fulfill this goal use parameter *edge_threshold*.  
From documentation:  
> edge_threshold : str, number or None, optional (default=None)  
        If it is a number only connections of amplitude greater than threshold will be shown.  
        If it is a string it must finish with a percent sign,
        e.g. "25.3%", and only connections of amplitude above the
        given percentile will be shown.

So let's display only connections that have weight property higher than value 0.5.

In [ ]:
view_connectome_3d(G, edge_threshold=0.5)

### Plot connectome with adjusted colormap

You have probably noticed that the colormap in the above-produced plot is symmetric, which means that the range is from -vmax to vmax. 

To adjust the colormap to be in the interval [0,vmax], set the parameter *symmetric_cmap* to False.


In [ ]:
view_connectome_3d(G, edge_threshold=0.5, symmetric_cmap=False)

The colormap of the newly-created plot is identical to the previous one. The reason is that in Graph G there are edges that have negative weights.

In [ ]:
# keep the count of negative weights
negative_weights = 0

for edge in G.edges():
    if (G.edges[edge]["weight"]) < 0:
        negative_weights += 1

print("The number of negative weights = ", negative_weights)

### View connectome with different parameters

Short description of other parameters:
- edge_cmap - colormap for edges (default "Spectral_r");  
- linewidth - width of edges (default 6.0);  
- node_size - size of nodes (default 3.0;  

In [ ]:
view_connectome_3d(G, edge_threshold=0.5, symmetric_cmap=False, edge_cmap="cool", linewidth=3, node_size=3)

## Plot Connectome 

Plot connectome on top of the brain glass schematics.


\- using [`nilearn.plotting.plot_connectome() tool`](https://nilearn.github.io/modules/generated/nilearn.plotting.plot_connectome.html#nilearn.plotting.plot_connectome)

### Import the code you need: `plot_connectome`

In [ ]:
from scona.visualisations import plot_connectome

### Plot Connectome

We only need the BrainNetwork Graph to produce plot of connectome in different orientations.  

*Important*: Graph has to contain nodes coordinates as a nodal attribute "centroids".

#### Default settings

By default, connectome is displayed in the 'ortho' orthogonal directions. Color of each edge is chosen based on the *weight* value of an edge. The default colormap for visualising edges - "bwr" (diverging colormap).

### Look at the data

In [ ]:
G10.number_of_nodes()

In [ ]:
G10.number_of_edges()

*Note*: One can efficiently use this functionality only for a small number of nodes and edges.  

That's why plotting Graph (even thresholded at cost 10) with 308 nodes and 4728 edges is not recommended, as you will not be able to visualise data and results from brain analysis efficiently.

In [ ]:
# plot BrainNetwork Graph G, the one constructed from MRI dataset

# plot_connectome(G10)

### Plot high-degree nodes and connections between them

#### Select top 10 nodes with the highest degree values

In [ ]:
# get the number of edges incident to each node

degrees = list(dict(G10.degree()).values())

In [ ]:
degrees

In [ ]:
# get the nodes that have the most connections to other nodes

def Nmaxelements(degrees, N):
    """
    Choose top <N> largest values in degrees list
    """
    final_list = [] 
  
    for i in range(0, N):  
        
        # find max
        max1 = 0
        for j in range(len(degrees)):      
            if degrees[j] > max1: 
                max1 = degrees[j]
        
        # get the index of max value
        index = degrees.index(max1)
        
        # set the index of max value to 0 in order not to break the order
        degrees[index] = 0
        
        # store the node (index) that has the max value
        final_list.append(index) 
    
    return final_list

In [ ]:
# select 10 most well-connected nodes in Graph G10

TopDegreeNodes = Nmaxelements(degrees, 10)

In [ ]:
TopDegreeNodes

By using [`networkx.Graph.subgraph`](https://networkx.github.io/documentation/stable/reference/classes/generated/networkx.Graph.subgraph.html) we create a new Graph that contains only indicated nodes and the edges between those nodes.

In [ ]:
# create a new Graph that contains nodes stored in "TopDegreeNodes" list and connections between them

new_Graph = G10.subgraph(TopDegreeNodes)

In [ ]:
type(new_Graph)

In [ ]:
# get the nodes in the new Graph

new_Graph.nodes()

In [ ]:
# get the edges in the new Graph

new_Graph.edges()

In [ ]:
new_Graph.edges[34,190]

Now we have created a new Graph that can be easily visualised by calling `plot_connectome`

In [ ]:
plot_connectome(new_Graph)

There are a bunch of parameters to to adjust the plot according to your preferences.  

For example, let's plot edges in other color than red and reduce the edgewidth.

All edges are plotted in red color, because the *weight* of each node equals to 1. That's why the default colormap used for representing the strength of the edges maps each node to the "maximum" color - red.

In [ ]:
for edge in new_Graph.edges():
    print("The weight of the edge {} is {}".format(edge, new_Graph.edges[edge]["weight"]))

Changing the colormap to "Spectral" will plot all edges in - "dark purple" color - the "maximum" color in "Spectral" colormap.

In [ ]:
plot_connectome(new_Graph, edge_cmap="Spectral")

But to change the edgewidth we need to pass *edge_kwargs* parameter, which is represented as a dictionary.  

In [ ]:
# dict to store the parameters for edges
edge_params = {}

In [ ]:
edge_params["linewidth"] = 2

And by passing *edge_kwargs* parameter to `plot_connectome` we can also indicate the color of edges.

In [ ]:
edge_params["color"] = "lightblue"

### Modified Plot of high-degree nodes and connections between them

In [ ]:
plot_connectome(new_Graph, edge_kwargs=edge_params)

### Plot connectome with different parameters

Short description of other parameters:
- output_file - The name of an image file to export the plot to;  
*Note*: plot will be saved to the given path and it will not be displayed in the notebook.  
By default, plot will be saved in the png format in the current directory unless the full path is given.   
  
- display_mode - Choose the direction of the cuts;  

- black_bg - If True, the background of the image is set to be black;

- node_color - color(s) of the nodes, if array, make sure to have the same length of node_color as the number of nodes;

- node_size - size(s) of the nodes;

Plot top 10 well-connected nodes in *'l' - sagittal left hemisphere only*, in *'z' - axial* and in *'r' - sagittal right hemisphere only* orientations;   
Plot in the black background;  
Use colors from current seaborn palette to plot nodes;  
Change the default size (50) of nodes to 70;  


In [ ]:
# get the colors from seaborn palette
current_palette = sns.color_palette()

# show colors in palette
sns.palplot(current_palette)

In [ ]:
# plot connectome with different parameters

plot_connectome(new_Graph, display_mode="lzr", black_bg=True, node_color=current_palette, node_size=70)

In [ ]:
display.close()